# word2vec as Matrix Factorization

Let's start with a simple training set.

In [1]:
train = ['The student speaks, as the student wants to learn. We learn what the student wants.']

In [2]:
# (Later)
# There are plenty of books freely available online!
# The Adventures of Sherlock Holmes by Arthur Conan Doyle
# http://www.gutenberg.org/ebooks/1661
'''!wget http://www.gutenberg.org/files/1661/1661-0.txt
with open('1661-0.txt') as f:
    train = [f.read()]'''

In [2]:
# (Even later)
# Bigger dataset of 100 MB (17M words)
'''!wget http://mattmahoney.net/dc/text8.zip
!unzip text8.zip'''
with open('text8') as f:
    train = [f.read()]

In [3]:
len(train[0].split()), 'words'

(17005207, 'words')

First, let's standardize the text (lowercase, remove punctuation, etc.).

In [4]:
%%time
from sklearn.feature_extraction.text import CountVectorizer

transformer = CountVectorizer()
transformer.fit(train)
analyzer = transformer.build_analyzer()

tokens = analyzer(train[0])
#print(tokens)

CPU times: user 11.6 s, sys: 1.41 s, total: 13 s
Wall time: 11.6 s


In [5]:
encoder = transformer.vocabulary_
#encoder

In [6]:
decoder = transformer.get_feature_names()
#decoder

The context is a window of size `WINDOW_SIZE` around each word of the corpus.

If the corpus if $w_0, \ldots, w_{n - 1}$, the context of a word $w_i$ is all words $w_{i - L}, w_{i - L + 1}, \ldots, w_{i + L}$ where $L$ represents the `WINDOW_SIZE`.

Write a piece of code that builds a **word**-context count matrix. Be careful of corner cases.

**The** student $\rightarrow$ *student* is a context of ***The***, so we should increment that word-context pair  
The **student** speaks $\rightarrow$ *The* and *speaks* are contexts of ***student***  
student **speaks** as

In [16]:
%%time
from collections import Counter
from numba import jit

WINDOW_SIZE = 5  # Should be 1 as a start, then 5 for bigger corpuses
counts = Counter()  # Should contain the number of word-context occurrences (keys are pairs)
nb_word = Counter()  # Should contain the number of occurrences of each word
nb_context = Counter()  # Should contain the number of occurrences of each context

#@jit(nopython=True)
def compute_counts(tokens):
    '''counts = dict()
    nb_word = dict()
    nb_context = dict()
    counts[('a', 'b')] = 0
    nb_word['a'] = 0
    nb_context['a'] = 0'''
    for pos, word in enumerate(tokens):
        for context in tokens[max(pos - WINDOW_SIZE, 0):pos] + tokens[pos + 1:pos + WINDOW_SIZE + 1]:
            '''if (word, context) not in counts:
                counts[word, context] = 0
            if word not in nb_word:
                nb_word[word] = 0
            if context not in nb_context:
                nb_context[context] = 0'''
            counts[word, context] += 1
            nb_word[word] += 1
            nb_context[context] += 1
    return counts, nb_word, nb_context
# Check counts
# 2 min 51 s on text8 (5 min 26 with numba)

counts, nb_word, nb_context = compute_counts(tokens)

CPU times: user 2min 47s, sys: 1.51 s, total: 2min 48s
Wall time: 2min 48s


We will now build a word-context PMI matrix (*pointwise mutual information*), empirically given by:

$$ PMI(w, c) = \log \frac{P(w, c)}{P(w)P(c)} = \log \frac{\#(w, c) |D|}{\#(w) \#(c)} $$

where $|D|$ is the number of words in the corpus, $\#(w), \#(c), \#(w, c)$ are respectively the number of occurrences of word, context and word-context pair.

This matrix will be sparse: please populate `rows`, `cols`, and `data` lists, for word indices (using `encoder` defined as vocabulary), contexts, and counts.

In [17]:
%%time
import numpy as np

rows = []  # Contains words indices
cols = []  # Contains context indices
data = []  # Contains values of the matrix

for (word, context), count in counts.items():
    if word == 'a':
        continue
    if context == 'a':
        continue
    rows.append(encoder[word])
    cols.append(encoder[context])
    data.append(np.log(count * len(tokens) / (nb_word[word] * nb_context[context])))

rows[:5], cols[:5], data[:5]

CPU times: user 40 s, sys: 532 ms, total: 40.5 s
Wall time: 40.5 s


([8957, 8957, 8957, 8957, 8957],
 [164918, 14302, 224516, 162480, 1131],
 [-0.054552883604456266,
  -1.4522145971706266,
  -0.6446473015805738,
  -2.0165973268025508,
  -0.03939306568843435])

In [18]:
from scipy.sparse import csr_matrix
from scipy.sparse.linalg import svds

pmi = csr_matrix((data, (rows, cols)), shape=(len(nb_word), len(nb_context)))
pmi

<253828x253828 sparse matrix of type '<class 'numpy.float64'>'
	with 32690878 stored elements in Compressed Sparse Row format>

In [19]:
ppmi = pmi.copy()
ppmi.data[ppmi.data < 0] = 0
ppmi.eliminate_zeros()
ppmi

<253828x253828 sparse matrix of type '<class 'numpy.float64'>'
	with 15068895 stored elements in Compressed Sparse Row format>

We are going to compute the SVD of this matrix to reduce the dimensionality.

The (compact) singular value decomposition of a $m \times n$ matrix $M$ of rank $r$ is $U \Sigma V^T$ where:

- $U$ is semi-unitary and of size $m \times r$
- $\Sigma$ is diagonal, $r \times r$
- $V^T$ is semi-unitary and of size $r \times n$, i.e. $U^T U = V^T V = I_{r \times r}$.

We usually order the singular values in decreasing order, to explain as much variance as possible ($k$-SVD is the best approximation of rank $k$).

In [22]:
%%time
u, sigma, vt = svds(ppmi, k=100)
# 1 min 55 s on text8

CPU times: user 8min 27s, sys: 3min 23s, total: 11min 51s
Wall time: 1min 38s


In [23]:
pmi.min(), pmi.max(), ppmi.min(), ppmi.max()

(-7.240258863549911, 12.005967839922151, 0.0, 12.005967839922151)

In [24]:
embeddings = u * sigma
embeddings.shape

(253828, 100)

In [15]:
u.shape, sigma.shape, vt.shape

((9, 3), (3,), (3, 9))

## Word similarity

Now let's play with embeddings!

Implement the cosine similarity:

$$ cos(u, v) = \frac{\langle u, v \rangle}{|| u ||_2 || v ||_2} $$

then check that you have the same results as `sklearn`.

It is now the moment to move to the Sherlock Holmes corpus. Go back to first cell!

Pick a few words in the vocabulary (`encoder`) and compute their 20 closest neighbors. 

In [25]:
from sklearn.metrics.pairwise import cosine_similarity

scores = cosine_similarity(embeddings[1].reshape(1, -1), embeddings).reshape(-1)
sorted(zip(scores, decoder))[-20:]

[(0.7510739167300924, 'stbase'),
 (0.7519782820567305, 'uua'),
 (0.7534333549770349, 'uac'),
 (0.753531637846724, 'cgg'),
 (0.7552023476748682, 'cuc'),
 (0.7553463894346881, 'aca'),
 (0.7554552144725636, 'aug'),
 (0.7574871433525748, 'aag'),
 (0.7599920655132323, 'ccg'),
 (0.7685452990846857, 'ggg'),
 (0.7700167503920008, 'uuu'),
 (0.7957665351104706, 'cga'),
 (0.7989154776149979, 'aaabbbccc'),
 (0.807071084372715, 'mudhens'),
 (0.8327737592610778, 'aau'),
 (0.8375506178121437, 'caa'),
 (0.887481921395474, 'boldsymbolbccc'),
 (0.906520170311129, 'boldsymbolccc'),
 (0.9078599968313081, 'aaab'),
 (1.0000000000000002, 'aaa')]

Actually, the similarity values have noise. Let's remove the negative values from the PMI matrix.

> *When  representing  words,  there  is  some  intuition  behind  ignoring  negative  values:  humans  can easily think of positive associations (e.g.  “Canada” and “snow”) but find it much harder to invent negative ones (“Canada” and “desert”).  This suggests that the perceived similarity of two words is more influenced by the positive context they share than by the negative context they share.  It therefore makes some intuitive sense to discard the negatively associated contexts and mark them as “uninformative” (0) instead*

It is now a PPMI matrix: positive pointwise mutual information.

In [17]:
ppmi = pmi.copy()
ppmi.data[ppmi.data < 0] = 0
ppmi.eliminate_zeros()  # Remove the now-zero values
ppmi
# Now recompute the SVD with ppmi

<9x9 sparse matrix of type '<class 'numpy.float64'>'
	with 10 stored elements in Compressed Sparse Row format>

## Semantic analogies

Now **let's replace logic with algebra.**

(Not everyone will be satisfied with this statement, I guess.)

Recompute the PPMI matrix and embeddings for the bigger dataset, `text8`.

Then attempt to answer some questions where we have to find $b^*$ in:

$$ a \textrm{ is to } a^* \textrm{ as } b \textrm{ is to } b^* $$

(ex. *Paris is to France as Tokyo is to Japan*)

How to express this in terms of embeddings?

In [18]:
# Once text8 has been trained
# encoder['paris'], encoder['france'], encoder['tokyo'], encoder['japan']
# a a* b (b*?)

Does it work? You may want to normalize the embeddings. Please do so into `embed_unit`.

Please look for nasty analogies (shortcuts that are unfair).

In [26]:
embed_unit = embeddings / np.linalg.norm(embeddings, axis=1)[:, None]

In [28]:
encoder['paris'], encoder['france'], encoder['tokyo'], encoder['japan']

(169210, 82530, 228252, 114173)

In [40]:
query = embed_unit[encoder['france']] - embed_unit[encoder['paris']] + embed_unit[encoder['tokyo']]

In [49]:
def answer(query, n_results=5):
    scores = cosine_similarity(query.reshape(1, -1), embed_unit).reshape(-1)
    return sorted(zip(scores, decoder))[-n_results:][::-1]

In [42]:
answer(query)

[(0.8694952035024651, 'japan'),
 (0.8640991007366399, 'tokyo'),
 (0.8146306894531837, 'yokkaichi'),
 (0.8131203127044921, 'tomakomai'),
 (0.8027972365105472, 'shiogama')]

In [43]:
query = embed_unit[encoder['france']] - embed_unit[encoder['paris']] + embed_unit[encoder['bangkok']]

In [54]:
answer(query, 20)

[(0.8662440898935503, 'berlin'),
 (0.8473603458619845, 'germany'),
 (0.7833771406686559, 'munich'),
 (0.7486081934362379, 'garching'),
 (0.7359592398999731, 'brandenburg'),
 (0.7354399816061715, 'erding'),
 (0.7343742311574561, 'frankfurt'),
 (0.729911816144808, 'hamburg'),
 (0.729031387009343, 'teilb'),
 (0.7271518177669145, 'elsterwerda'),
 (0.7263975891410023, 'neubrandenburg'),
 (0.7253795822362665, 'magdeburg'),
 (0.7239664256507696, 'fermats'),
 (0.7214952728047794, 'rstenfeldbruck'),
 (0.7196846927967593, 'stadt'),
 (0.7189303566021182, 'sachsen'),
 (0.7185047044672557, 'elate'),
 (0.718356748508607, 'staatskapelle'),
 (0.7165728716425435, 'musikakademie'),
 (0.715094317540743, 'thomanerchor')]

In [50]:
query = embed_unit[encoder['wedding']]

In [52]:
answer(query, 20)

[(1.0000000000000002, 'wedding'),
 (0.9133136794969166, 'bride'),
 (0.8979694437616739, 'couple'),
 (0.8759742132836135, 'deceased'),
 (0.8734303279235454, 'loved'),
 (0.8727106446166029, 'rachel'),
 (0.8694234185229168, 'herself'),
 (0.8630216313703281, 'sisters'),
 (0.8437748629009066, 'funeral'),
 (0.8384753853049091, 'beloved'),
 (0.8245934901409449, 'prostitute'),
 (0.8221449242658535, 'osmotar'),
 (0.8133264428325211, 'maid'),
 (0.8081776392996407, 'lover'),
 (0.8034274925386586, 'wives'),
 (0.8025489203869436, 'servant'),
 (0.8025069131905446, 'visits'),
 (0.8019771929976923, 'marry'),
 (0.8000336526875786, 'phoebe'),
 (0.7993126796993985, 'husband')]

In [53]:
query = embed_unit[encoder['france']] - embed_unit[encoder['paris']] + embed_unit[encoder['berlin']]
answer(query, 20)

[(0.8662440898935503, 'berlin'),
 (0.8473603458619845, 'germany'),
 (0.7833771406686559, 'munich'),
 (0.7486081934362379, 'garching'),
 (0.7359592398999731, 'brandenburg'),
 (0.7354399816061715, 'erding'),
 (0.7343742311574561, 'frankfurt'),
 (0.729911816144808, 'hamburg'),
 (0.729031387009343, 'teilb'),
 (0.7271518177669145, 'elsterwerda'),
 (0.7263975891410023, 'neubrandenburg'),
 (0.7253795822362665, 'magdeburg'),
 (0.7239664256507696, 'fermats'),
 (0.7214952728047794, 'rstenfeldbruck'),
 (0.7196846927967593, 'stadt'),
 (0.7189303566021182, 'sachsen'),
 (0.7185047044672557, 'elate'),
 (0.718356748508607, 'staatskapelle'),
 (0.7165728716425435, 'musikakademie'),
 (0.715094317540743, 'thomanerchor')]

Please note that it is possible to reuse your factorization method to learn the embeddings. This is the topic of a future homework!

# References

Great reads!

Levy, O., & Goldberg, Y. (2014). [Neural word embedding as implicit matrix factorization.](https://papers.nips.cc/paper/5477-neural-word-embedding-as-implicit-matrix-factorization.pdf) In Advances in neural information processing systems (pp. 2177–2185).

Doyle, A. C. (1891). [The Adventures of Sherlock Holmes: Adventure I. — A Scandal in Bohemia.](http://www.gutenberg.org/ebooks/1661) The Strand Magazine, vol. 2, pp. 61–75 (July 1891). 